In [1]:
%matplotlib inline

In [1]:
from __future__ import division

import sys
import time
import logging
import numpy as np
from scipy.io import loadmat
from os import path

# change this to the path of mushu if you don't have it in your
# PYTHONPATH already
sys.path.append('../../mushu')
sys.path.append('../')

import libmushu
from libmushu.driver.replayamp import ReplayAmp
from wyrm.types import RingBuffer
import wyrm.processing as proc
from wyrm import io
from wyrm.types import Data, BlockBuffer, RingBuffer
from pandas import read_csv      

#Classifiers
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn import metrics
import matplotlib
import matplotlib.pyplot as plt

from sklearn.externals import joblib
from os import listdir
from os.path import isfile, join

DEBUG:matplotlib:$HOME=C:\Users\aleja
DEBUG:matplotlib:matplotlib data path C:\Users\aleja\Anaconda3\lib\site-packages\matplotlib\mpl-data
DEBUG:matplotlib:loaded rc file C:\Users\aleja\Anaconda3\lib\site-packages\matplotlib\mpl-data\matplotlibrc
DEBUG:matplotlib:matplotlib version 2.2.2
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is win32
DEBUG:matplotlib:loaded modules: ['builtins', 'sys', '_frozen_importlib', '_imp', '_warnings', '_thread', '_weakref', '_frozen_importlib_external', '_io', 'marshal', 'nt', 'winreg', 'zipimport', 'encodings', 'codecs', '_codecs', 'encodings.aliases', 'encodings.utf_8', '_signal', '__main__', 'encodings.latin_1', 'io', 'abc', '_weakrefset', '_bootlocale', '_locale', 'encodings.cp1252', 'site', 'os', 'errno', 'stat', '_stat', 'ntpath', 'genericpath', 'os.path', '_collections_abc', '_sitebuiltins', 'sysconfig', 'types', 'functools', '_functools', 'collections', 'operator', '_operator', 'keyword', 'heapq', '_heapq', 'itertools', 'reprl

DEBUG:matplotlib:CACHEDIR=C:\Users\aleja\.matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from C:\Users\aleja\.matplotlib\fontList.json
DEBUG:matplotlib.backends:backend module://ipykernel.pylab.backend_inline version unknown
DEBUG:matplotlib.backends:backend module://ipykernel.pylab.backend_inline version unknown


In [2]:
logging.basicConfig(format='%(relativeCreated)10.0f %(threadName)-10s %(name)-10s %(levelname)8s %(message)s', level=logging.NOTSET)
logger = logging.getLogger(__name__)

In [3]:
# replay the experiment in real time?
REALTIME = False


TRAIN_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Train.mat'
TEST_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Test.mat'

TRAIN_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Train.mat'
TEST_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Test.mat'


CHANNEL_DATA = '../BCI_Comp_III_Wads_2004/data/eloc64.txt'

TRUE_LABELS_TEST = "WQXPLZCOMRKO97YFZDEZ1DPI9NNVGRQDJCUVRMEUOOOJD2UFYPOO6J7LDGYEGOA5VHNEHBTXOO1TDOILUEE5BFAEEXAW_K4R3MRU"

STIMULUS_CODE = {
    # cols from left to right
    1 : "agmsy5",
    2 : "bhntz6",
    3 : "ciou17",
    4 : "djpv28",
    5 : "ekqw39",
    6 : "flrx4_",
    # rows from top to bottom
    7 : "abcdef",
    8 : "ghijkl",
    9 : "mnopqr",
    10: "stuvwx",
    11: "yz1234",
    12: "56789_"
}

MARKER_DEF_TRAIN = {'target': ['target'], 'nontarget': ['nontarget']}
MARKER_DEF_TEST = {i : [i] for i in STIMULUS_CODE.values()}

SEG_IVAL = [0, 800]

In [4]:
def load_bci_TESTdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][60:,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][60:,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][60:,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[60:,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_m.get('TargetChar')[0][60:]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [5]:
def load_bci_TRAINdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][:60,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][:60,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][:60,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[:60,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_m.get('TargetChar')[0][:60]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [6]:
def train(filename):
    cnt = load_bci_TRAINdata(filename)

    fs_n = cnt.fs / 2

    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    cnt = proc.lfilter(cnt, b, a)

#     b, a = proc.signal.butter(5, [.4 / fs_n], btype='high')
#     cnt = proc.lfilter(cnt, b, a)

    cnt = proc.subsample(cnt, 20)

    epo = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL)

    #from wyrm import plot
    #plot.plot_spatio_temporal_r2_values(proc.sort_channels(epo))
    #print JUMPING_MEANS_IVALS
    #plot.plt.show()

    fv = proc.create_feature_vectors(epo)
    X = fv.data
    y = fv.axes[0]
#     X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size = 0.3, train_size = 0.7)

    #     clf = proc.lda_train(fv)
    clf = LinearDiscriminantAnalysis(solver='eigen')
    clf.fit(X,y)
    return clf

In [7]:


from __future__ import division

import time

import numpy as np

from libmushu.amplifier import Amplifier


class RReeplayAmp(Amplifier):

    def configure(self, data, marker, channels, fs, realtime=True, blocksize_ms=None, blocksize_samples=None):
        """

        Parameters
        ----------
        data
        marker
        channels
        fs
        realtime
        blocksize_ms : float
            blocksize in milliseconds
        blocksize_samples : int
            blocksize in samples

        Raises
        ------
        TypeError :
            if ``blocksize_ms`` and ``blocksize_s`` are given.

        """
        if [blocksize_ms, blocksize_samples].count(None) != 1:
            raise TypeError("blocksize_ms and blocksize_samples are mutually exclusive.")

        self.data = data
        # slow python
        self.marker = marker
        # fast numpy
        self.marker_ts = np.array([ts for ts, s in marker]) #marker time_sample
        self.marker_s = np.array([s for ts, s in marker]) #marker sample
        self.channels = channels
        self.fs = fs
        self.realtime = realtime

        if blocksize_ms:
            samples = fs * (blocksize_ms / 1000)
            if not samples.is_integer():
                raise ValueError("Resulting blocksize is not integer, please fix the blocksize_ms.")
            self.samples = samples
        if blocksize_samples:
            self.samples = blocksize_samples

    def start(self):
        self.last_sample_time = time.time()
        self.pos = 0

    def stop(self):
        pass

    def get_data(self):
        """

        Returns
        -------
        chunk, markers: Markers is time in ms since relative to the
        first sample of that block.

        """
        if self.realtime:
            elapsed = time.time() - self.last_sample_time
            blocks = (self.fs * elapsed) // self.samples
            samples = int(blocks * self.samples)
            
        else:
            samples = self.samples
      
        elapsed = samples / self.fs
        self.last_sample_time += elapsed
        # data
        chunk = self.data[self.pos:int(self.pos+samples)]
        #self.data = self.data[samples:]
        # markers

        # slow python version
        #markers = [x for x in self.marker if x[0] < elapsed * 1000]
        #self.marker = [x for x in self.marker if x[0] >= elapsed * 1000]
        #self.marker = [[x[0] - elapsed * 1000, x[1]] for x in self.marker]

        # fast numpy version
        mask = self.marker_ts < (elapsed * 1000) 
        markers = list(zip(self.marker_ts[mask], self.marker_s[mask]))
        self.marker_ts = self.marker_ts[~mask]
        self.marker_s = self.marker_s[~mask]
        self.marker_ts -= elapsed * 1000

        self.pos += samples
        return chunk, markers

    def get_channels(self):
        return self.channels

    def get_sampling_frequency(self):
        return self.fs

    @staticmethod
    def is_available():
        return True


In [22]:
def online_experiment(amp, cfy, subject):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    
    file = open('sim_training_LDA'+subject+'.txt', 'w')
    file.write('LDA Online simulation'+subject)
    
    # csv results file
    filename = 'results/'+subject+'/Results_LDA_'+subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)

    chfilename = 'results/'+subject+'/CharacterResults_LDA_'+subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames) 
    

    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [10 / fn], btype='low')
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
#     zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # low-pass and subsample
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
#         cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        cnt = proc.subsample(cnt, 20)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, SEG_IVAL, newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL, newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = proc.create_feature_vectors(epo)
        fv_train = proc.create_feature_vectors(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        lda_out = cfy.predict_proba(fv.data)[:,1]
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict(fv.data) 
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

#         lda_out = proc.lda_apply(fv, cfy)
        # class_names = letters in matrix row/column
        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, lda_out)
        
        
        # Accumulated metrics
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
               
              
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, n_trial))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                           current_letter, int(markers_processed/12)))

                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))
        

            markers_processed += 1

                
#             if (markers_processed%12 == 0) & (markers_processed != 180) & (not correct_letter):
#                 current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
#                 if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                     file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                   current_letter, int(markers_processed/12)))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
#                     correct_letter = True
           
#             elif markers_processed == 180: # 12 trials x 15 repetitions = 180
#                 endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
#                 # Set all probabilities to zero
#                 letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
#                 markers_processed = 0
#                 if not correct_letter:
#                     file.write('\n\nFailed to predict character #{} in 15 trials'.format(len(endresult)))
#                     file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
                    
#                 correct_letter = False
# #                 current_letter_idx += 1
# #                 print('letter idx', current_letter_idx)
# #                 current_letter = TRUE_LABELS[current_letter_idx].lower()
#             markers_processed += 1
#         print(letter_prob)
#         logger.debug("".join([i[0] for i in sorted(letter_prob.items(), key=lambda x: x[1], reverse=True)]).replace(current_letter, " %s " % current_letter))

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()
    resultsFile.close()

    amp.stop()


In [33]:
subject = 'B'
if subject == 'A':
    TRAIN_DATA = TRAIN_DATA_A
    TEST_DATA = TRAIN_DATA_A
elif subject == 'B':
    TRAIN_DATA = TRAIN_DATA_B
    TEST_DATA = TRAIN_DATA_B  

data_m = loadmat(TRAIN_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars

In [34]:
TRUE_LABELS

'KOJDWZEUEWWFOEBHXTQTTZUMO'

# 1. Training (off-line)

In [37]:
clf = train(TRAIN_DATA)

In [38]:
filename = 'Trained Classifiers/'+subject+'/LDA_'+subject+'.pkl'

In [39]:
# joblib.dump(clf, filename)

['Trained Classifiers/B/LDA_B.pkl']

In [40]:
clf = joblib.load(filename)

# 2. Online experiment

In [41]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TEST_DATA)

In [42]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [43]:
online_experiment(amp, clf, subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 
DEBUG:__main__:5
DEBUG:__main__:Markers processed: 
DEBUG:__main__:6
DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8


Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 11.968374252319336
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 11.967897415161133
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.3333333333333333
time 11.961698532104492
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 10.971307754516602
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6
time 12.966394424438477
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 12.967348098754883
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classificati

DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 



P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.7777777777777778
time 15.956401824951172
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.5 	f1:  0.5 	accuracy:  0.8
time 13.960838317871094
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.5 	f1:  0.5 	accuracy:  0.8181818181818182
time 47.86944389343262
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  0.5 	f1:  0.4 	accuracy:  0.75
time 13.953685760498047
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  0.5 	f1:  0.4 	accuracy:  0.7692307692307693
time 11.96742057800293


DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18


...

 	precision:  0.48859934853420195 	f1:  0.5477784540474742 	accuracy:  0.8286439114391144
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 51.8643856048584
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.6232686980609419 	precision:  0.48859934853420195 	f1:  0.5477784540474742 	accuracy:  0.828683421720083
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 31.914472579956055
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.6232686980609419 	precision:  0.4880694143167028 	f1:  0.5474452554744526 	accuracy:  0.8284923928077456
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 43.42341423034668
Predicho:  [0] 	Verdadero:  [0] [ True]


DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eojdwveuewwfoebhxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eojdwveuewwfoebhxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eojdwveuewwfoebhxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eojdwveuewwfoebhxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179



P300 classification metrics...
recall:  0.6232686980609419 	precision:  0.4880694143167028 	f1:  0.5474452554744526 	accuracy:  0.8285319197971883
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 21.939992904663086
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.623789764868603 	precision:  0.4886240520043337 	f1:  0.5479951397326853 	accuracy:  0.8285714285714286
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 25.929689407348633
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.623789764868603 	precision:  0.4886240520043337 	f1:  0.5479951397326853 	accuracy:  0.8286109191430546
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 24.935007095336914
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.623789764868603 	precision:  0.4886240

DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eojdwveuewwfoebhxtqttzu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:eojdwveuewwfoebhxtqttzum



P300 classification metrics...
recall:  0.623789764868603 	precision:  0.4886240520043337 	f1:  0.5479951397326853 	accuracy:  0.8286898457287589
Character prediction metrics...
Current accuracy: 91.30434782608695
23/25 characters predicted
time 23.451566696166992
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.6229281767955801 	precision:  0.4886240520043337 	f1:  0.5476624165148756 	accuracy:  0.8284990791896869
Character prediction metrics...
Current accuracy: 91.66666666666666
24/25 characters predicted
Accuracy: 91.66666666666666


# INTERSUJETO

In [45]:
def online_experiment_intersujeto(amp, cfy, inter_subject):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    
    file = open('sim_training_LDA'+inter_subject+'.txt', 'w')
    file.write('LDA Online simulation'+inter_subject)
    
    # csv results file
    filename = 'results/Intersujeto/'+inter_subject+'/Results_LDA_'+inter_subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)

    chfilename = 'results/Intersujeto/'+inter_subject+'/CharacterResults_LDA_'+inter_subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames) 
    

    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [10 / fn], btype='low')
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
#     zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # low-pass and subsample
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
#         cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        cnt = proc.subsample(cnt, 20)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, SEG_IVAL, newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL, newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = proc.create_feature_vectors(epo)
        fv_train = proc.create_feature_vectors(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        lda_out = cfy.predict_proba(fv.data)[:,1]
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict(fv.data) 
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

#         lda_out = proc.lda_apply(fv, cfy)
        # class_names = letters in matrix row/column
        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, lda_out)
        
        
        # Accumulated metrics
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
               
              
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, n_trial))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                           current_letter, int(markers_processed/12)))

                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))
        

            markers_processed += 1

                
#             if (markers_processed%12 == 0) & (markers_processed != 180) & (not correct_letter):
#                 current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
#                 if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                     file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                   current_letter, int(markers_processed/12)))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
#                     correct_letter = True
           
#             elif markers_processed == 180: # 12 trials x 15 repetitions = 180
#                 endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
#                 # Set all probabilities to zero
#                 letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
#                 markers_processed = 0
#                 if not correct_letter:
#                     file.write('\n\nFailed to predict character #{} in 15 trials'.format(len(endresult)))
#                     file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
                    
#                 correct_letter = False
# #                 current_letter_idx += 1
# #                 print('letter idx', current_letter_idx)
# #                 current_letter = TRUE_LABELS[current_letter_idx].lower()
#             markers_processed += 1
#         print(letter_prob)
#         logger.debug("".join([i[0] for i in sorted(letter_prob.items(), key=lambda x: x[1], reverse=True)]).replace(current_letter, " %s " % current_letter))

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()
    resultsFile.close()

    amp.stop()


In [55]:
inter_subject = 'B-clfA'
if inter_subject == 'A-clfB':
    TEST_DATA = TRAIN_DATA_A
    subject = 'B'
elif inter_subject == 'B-clfA':
    TEST_DATA = TRAIN_DATA_B  
    subject = 'A'
data_m = loadmat(TEST_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars
TRUE_LABELS

'KOJDWZEUEWWFOEBHXTQTTZUMO'

## 1. Training (off-line)

In [56]:
# load classifier
filename = 'Trained Classifiers/'+subject+'/LDA_'+subject+'.pkl'
clf = joblib.load(filename)

## 2. Online experiment

In [57]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TEST_DATA)

In [58]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [59]:
online_experiment_intersujeto(amp, clf, inter_subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 
DEBUG:__main__:5
DEBUG:__main__:Markers processed: 
DEBUG:__main__:6
DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8
DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers p

Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 7.973909378051758
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 7.977485656738281
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 8.977651596069336
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 7.979154586791992
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 8.975982666015625
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.16666666666666666
time 7.978916168212891
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall

DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 



P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.2727272727272727
time 9.972810745239258
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  0.14285714285714285 	f1:  0.2 	accuracy:  0.3333333333333333
time 9.972572326660156
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  0.14285714285714285 	f1:  0.2 	accuracy:  0.38461538461538464
time 8.975982666015625
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  0.14285714285714285 	f1:  0.2 	accuracy:  0.42857142857142855
time 8.97669792175293
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.3333333333333333 	precision:  0.14285714285714285 	f1:  0.2 	accuracy:  0.4666666666666667
time 9.973287582397461
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.33

DEBUG:__main__:19
DEBUG:__main__:Markers processed: 
DEBUG:__main__:20
DEBUG:__main__:Markers processed: 
DEBUG:__main__:21
DEBUG:__main__:Markers processed: 
DEBUG:__main__:22
DEBUG:__main__:Markers processed: 
DEBUG:__main__:23
DEBUG:__main__:Markers processed: 
DEBUG:__main__:24


...

Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.32409972299168976 	precision:  0.20598591549295775 	f1:  0.2518837459634015 	accuracy:  0.6789838337182448
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 17.952442169189453
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.32409972299168976 	precision:  0.20598591549295775 	f1:  0.2518837459634015 	accuracy:  0.6790579542830755
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 19.947052001953125
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.32409972299168976 	precision:  0.20598591549295775 	f1:  0.2518837459634015 	accuracy:  0.6791320406278855
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 18.950223922729492
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics..

DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:172
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:173
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:174
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:175
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c


Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 20.946025848388672
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.32409972299168976 	precision:  0.20580474934036938 	f1:  0.2517482517482517 	accuracy:  0.6791974169741697
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 32.9129695892334
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.32409972299168976 	precision:  0.20580474934036938 	f1:  0.2517482517482517 	accuracy:  0.6792713857505188
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 15.957117080688477
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.32409972299168976 	precision:  0.20580474934036938 	f1:  0.2517482517482517 	accuracy:  0.6793453204241586
Character prediction metrics...
Current accuracy: 13.043478260869565
23/

DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5c
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:foj3cvd8b3skrbyxonpte5cq


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.3236514522821577 	precision:  0.2054433713784021 	f1:  0.2513426423200859 	accuracy:  0.6788758350610459
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 21.943092346191406
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.3236514522821577 	precision:  0.20526315789473684 	f1:  0.25120772946859904 	accuracy:  0.6787194841087056
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 22.937774658203125
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.3236514522821577 	precision:  0.20526315789473684 	f1:  0.25120772946859904 	accuracy:  0.678793460741423
Character prediction metrics...
Current accuracy: 13.043478260869565
23/25 characters predicted
time 19.94800567626953
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
re

## Sujeto C

In [159]:
def load_bci_TRAINdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[:30,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [158]:
def load_bci_TESTdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[30:,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [136]:
labels = 'CATDOGFISHWATERBOWLHATHATGLOVESHOESFISHRAT'
path_ = '../BCI_Comp_II_2003/data/'
datafiles = [join(path_,f) for f in listdir(path_) if isfile(join(path_, f))]
training_set = [f for i,f in enumerate(datafiles) if '12' not in f and 'eloc64' not in f]
testing_set = [f for i,f in enumerate(datafiles) if '12' in f and 'eloc64' not in f]

In [160]:
# load the training set
dat_train = load_bci_TRAINdata2(training_set)


In [161]:
TRUE_LABELS = labels[30:]
TRUE_LABELS

'SHOESFISHRAT'

### Training

In [162]:
def train_d2(dat):
    cnt = dat

    fs_n = cnt.fs / 2

    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    cnt = proc.lfilter(cnt, b, a)

#     b, a = proc.signal.butter(5, [.4 / fs_n], btype='high')
#     cnt = proc.lfilter(cnt, b, a)

    cnt = proc.subsample(cnt, 20)

    epo = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL)

    #from wyrm import plot
    #plot.plot_spatio_temporal_r2_values(proc.sort_channels(epo))
    #print JUMPING_MEANS_IVALS
    #plot.plt.show()

    fv = proc.create_feature_vectors(epo)
    X = fv.data
    y = fv.axes[0]
#     X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size = 0.3, train_size = 0.7)

    #     clf = proc.lda_train(fv)
    clf = LinearDiscriminantAnalysis(solver='eigen')
    clf.fit(X,y)
    return clf

In [163]:
clf = train_d2(dat_train)

In [164]:
subject = 'C'
filename = 'Trained Classifiers/'+subject+'/LDA_'+subject+'.pkl'

In [165]:
joblib.dump(clf, filename)

['Trained Classifiers/C/LDA_C.pkl']

### Online experiment

In [166]:
bbuffer = BlockBuffer(12)
dat_test = load_bci_TESTdata2(training_set)
cnt = dat_test

In [167]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [168]:
online_experiment(amp, clf, subject)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 6.248712539672852
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 8.486509323120117
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 11.019706726074219
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.75
time 9.973526000976562
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8
time 9.972572326660156
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8333333333333334
time 11.989355087280273
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification 

DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14
DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 


Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  1.0 	f1:  0.8 	accuracy:  0.9090909090909091
time 11.415481567382812
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  1.0 	f1:  0.8 	accuracy:  0.9166666666666666
time 25.472402572631836
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  1.0 	f1:  0.8 	accuracy:  0.9230769230769231
time 18.075227737426758
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  0.6666666666666666 	f1:  0.6666666666666666 	accuracy:  0.8571428571428571
time 11.147260665893555
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  0.6666666666666666 	f1:  0.6666666666666666 	accuracy:  0.8666666666666667
time 11.968612670898438
Predicho:  [0] 	Verdadero:  [0

DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 
DEBUG:__main__:19
DEBUG:__main__:Markers processed: 
DEBUG:__main__:20
DEBUG:__main__:Markers processed: 
DEBUG:__main__:21
DEBUG:__main__:Markers processed: 
DEBUG:__main__:22
DEBUG:__main__:Markers processed: 


...

Character prediction metrics...
Current accuracy: 90.0
10/12 characters predicted
time 20.449161529541016
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5201698513800425 	f1:  0.6102117061021171 	accuracy:  0.8422379032258065
Character prediction metrics...
Current accuracy: 90.0
10/12 characters predicted
time 23.06509017944336
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5190677966101694 	f1:  0.6094527363184079 	accuracy:  0.8418136020151133
Character prediction metrics...
Current accuracy: 90.0
10/12 characters predicted
time 24.05071258544922
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5190677966101694 	f1:  0.6094527363184079 	accuracy:  0.8418932527693856
Character prediction metrics...
Current accuracy: 90.0
10/12 characters predicted
time 22.855520248413086
Predicho:  [0]

DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoesfisnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoesfisnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoesfisnr


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5168776371308017 	f1:  0.607940446650124 	accuracy:  0.8410462776659959
Character prediction metrics...
Current accuracy: 90.0
10/12 characters predicted
time 39.101600646972656
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5168776371308017 	f1:  0.607940446650124 	accuracy:  0.8411261940673705
Character prediction metrics...
Current accuracy: 90.0
10/12 characters predicted
time 36.810874938964844
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5168776371308017 	f1:  0.607940446650124 	accuracy:  0.8412060301507538
Character prediction metrics...
Current accuracy: 90.0


DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoesfisnra


10/12 characters predicted
time 61.072349548339844
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7379518072289156 	precision:  0.5168776371308017 	f1:  0.607940446650124 	accuracy:  0.8412857860371673
Character prediction metrics...
Current accuracy: 90.9090909090909
11/12 characters predicted
Accuracy: 90.9090909090909


In [14]:
a= list(np.arange(6))
b = [True, False, True, True, True, False]

In [15]:
a[~b]

TypeError: bad operand type for unary ~: 'list'

In [10]:
a

array([0, 1, 2, 3, 4, 5])